In [1]:
#importing the classes and functions
import pyspark
from pyspark import *
from pyspark.conf import *
from pyspark.sql import *

In [2]:
#setting the data files for users and their friend list
userdata_path = 'userdata.txt'
friendsdata_path = 'soc_file.txt'
app_name = 'Userdata and their Friends'
master = 'local'

In [3]:
#configuring the Spark and setting the master & app name
spark = SparkConf().setAppName(app_name).setMaster(master)
sc = SparkContext(conf=spark)

In [4]:
#creating the RDD from the inputfile
friends_data = sc.textFile(friendsdata_path)

#checking the input data
#for line in friends_data.collect():
#    print(line)

In [5]:
def mutual_friend_mapper(line):
    user_friends = line.split("\t")
    
    user = user_friends[0]
    friends = user_friends[1].split(",")
    
    friends_second_list = list(friends)
    mutual_friend_list = list()
    
    if friends:
        for friend in friends:
            if friend != '':
                friends_second_list.remove(friend)
                friends_first_list = list(friends_second_list)
                
                if int(friend) > int(user):
                    mutual_friend_list.append(((int(user), int(friend)), friends_first_list))
                    friends_second_list.append(friend)
                else:
                    mutual_friend_list.append(((int(friend), int(user)), friends_first_list))
                    friends_second_list.append(friend)
    
    _mutual_friend_list = list()
    
    for line in mutual_friend_list:
        temp = list(line)
        temp[0] = str(temp[0]).replace('(','').replace(')','')
        temp[1] = set(temp[1])
        line = list(temp)
        _mutual_friend_list.append(line)
        
    return _mutual_friend_list

In [6]:
temp = mutual_friend_mapper('9	0,6085,18972,19269')

print(temp)

'''for line in temp:
    temp = list(line)
    temp[0] = str(temp[0]).replace('(','').replace(')','')
    temp[1] = set(temp[1])
    line = list(temp)
    print(line)'''

[['0, 9', {'18972', '19269', '6085'}], ['9, 6085', {'18972', '19269', '0'}], ['9, 18972', {'0', '19269', '6085'}], ['9, 19269', {'0', '6085', '18972'}]]


"for line in temp:\n    temp = list(line)\n    temp[0] = str(temp[0]).replace('(','').replace(')','')\n    temp[1] = set(temp[1])\n    line = list(temp)\n    print(line)"

In [7]:
paired_data_rdd = friends_data.flatMap(mutual_friend_mapper)

mutual_friends_rdd = paired_data_rdd.reduceByKey(lambda list1, list2: len(list1.intersection(list2))).filter(lambda x: x[1] != 0)

mutual_friends_rdd.saveAsTextFile('spark_rdd_version/mutual_friends.txt')

In [8]:
top_ten_mutual_friends_rdd = mutual_friends_rdd.map(lambda y: (y[1], y[0])).sortByKey(ascending=False).collect()[0:10]

for line in top_ten_mutual_friends_rdd:
    print(line)

(99, '18666, 18668')
(99, '18670, 18679')
(99, '18676, 18712')
(99, '18676, 18721')
(99, '18681, 18707')
(99, '18683, 18688')
(99, '18683, 18710')
(99, '18683, 18728')
(99, '18685, 18696')
(99, '18688, 18710')


In [9]:
userdata_rdd = sc.textFile('userdata.txt')

friends_details_rdd = userdata_rdd.map(lambda x: x.split(",")).map(lambda x: (int(x[0]), x[1:]))

for line in friends_details_rdd.collect():
    print(line)

(0, ['Evangeline', 'Taylor', '3396 Rogers Street', 'Loveland', 'Ohio', '45140', 'US', 'Unfue1996', '1/24/1996'])
(1, ['Robert', 'Cottrell', '1775 Sycamore Circle', 'Dallas', 'Texas', '75234', 'US', 'Dinvis', '11/26/1973'])
(2, ['Kathryn', 'Winn', '2858 Jerry Dove Drive', 'Wampee', 'South Carolina', '29568', 'US', 'Couchisem', '9/29/1941'])
(3, ['Harry', 'Kowalewski', '3835 Romrog Way', 'Indianola', 'Nebraska', '69034', 'US', 'Scather', '5/21/1950'])
(4, ['Paula', 'McCoy', '4915 Aaron Smith Drive', 'York', 'Pennsylvania', '17404', 'US', 'Thandsoll', '10/28/1935'])
(5, ['Beth', 'Watson', '2149 Powder House Road', 'Lake Worth', 'Florida', '33463', 'US', 'Aullewon', '8/27/1970'])
(6, ['Mark', 'Berman', '1107 Roane Avenue', 'Houston', 'Texas', '77032', 'US', 'Latme1978', '8/21/1978'])
(7, ['David', 'Brown', '3427 Tuna Street', 'Pontiac', 'Michigan', '48342', 'US', 'Applay', '12/23/1970'])
(8, ['Sergio', 'McDonald', '2323 Rafe Lane', 'Memphis', 'Mississippi', '38104', 'US', 'Evered', '11/29/

(185, ['Shawn', 'Rowe', '1460 Woodrow Way', 'Houston', 'Texas', '77006', 'US', 'Suchied', '10/16/1975'])
(7272, ['Iva', 'Allen', '155 Henery Street', 'Wichita', 'Kansas', '67226', 'US', 'Eatied45', '3/4/1945'])
(7345, ['Marshall', 'Davis', '3706 Private Lane', 'Tifton', 'Georgia', '31794', 'US', 'Alimpragn', '7/27/1932'])
(12249, ['Marilyn', 'Sweet', '3475 Boundary Street', 'Jacksonville', 'Florida', '32207', 'US', 'Hend1947', '12/7/1947'])
(15141, ['Barbara', 'Jefferson', '4085 Ventura Drive', 'San Lucas', 'California', '93954', 'US', 'Poppy1953', '1/10/1953'])
(21149, ['Miriam', 'Sigman', '1647 Pinewood Avenue', 'Marquette', 'Michigan', '49855', 'US', 'Gosaing', '12/14/1968'])
(29810, ['Phillip', 'Taylor', '3295 Pearlman Avenue', 'Woburn', 'Massachusetts', '1801', 'US', 'Clictithe', '12/27/1959'])
(42317, ['Tonya', 'Winnett', '3524 Metz Lane', 'Woburn', 'Massachusetts', '1801', 'US', 'Grout1994', '1/8/1994'])
(43145, ['Anna', 'Coleman', '4092 Mount Street', 'Bancroft', 'Michigan', '4

(24632, ['Tracy', 'Pritchard', '487 Central Avenue', 'Jersey City', 'New Jersey', '7307', 'US', 'Softelp', '8/17/1962'])
(24847, ['Jo', 'Price', '4487 Rollins Road', 'Chappell', 'Nebraska', '69129', 'US', 'Womme1965', '1/9/1965'])
(25072, ['Wayne', 'Hicks', '1102 Lucky Duck Drive', 'Pittsburgh', 'Pennsylvania', '15210', 'US', 'Crithimard', '1/17/1934'])
(25809, ['Jeremy', 'Quintero', '690 Twin Oaks Drive', 'Grand Rapids', 'Michigan', '49503', 'US', 'Poters63', '9/9/1963'])
(25840, ['Alice', 'Dawson', '2702 Martha Street', 'Kingman', 'Arizona', '86401', 'US', 'Ower1996', '12/9/1996'])
(26395, ['Stephen', 'Landry', '4455 Rainbow Drive', 'North Canton', 'Ohio', '44720', 'US', 'Lostaing1976', '4/21/1976'])
(27394, ['Frances', 'Thurmond', '869 Stoney Lane', 'Richardson', 'Texas', '75081', 'US', 'Whind1938', '4/8/1938'])
(27847, ['Raymond', 'Reeves', '4528 Rainbow Drive', 'Youngstown', 'Ohio', '44512', 'US', 'Reirence', '9/29/1969'])
(28027, ['John', 'Stafford', '3598 Eastland Avenue', 'Jack

(40848, ['Barbara', 'Surber', '2498 Meadowview Drive', 'Waynesboro', 'Virginia', '22980', 'US', 'Thatholl', '12/12/1963'])
(47659, ['Robert', 'Liner', '811 Clousson Road', 'Sergeant Bluff', 'Iowa', '51054', 'US', 'Ataked', '5/23/1952'])
(8593, ['Alfonso', 'Holt', '1708 Cimmaron Road', 'Irvine', 'California', '92664', 'US', 'Difeed', '6/4/1942'])
(10469, ['William', 'Church', '2060 Locust Court', 'Artesia', 'California', '90701', 'US', 'Trailtoo', '12/8/1971'])
(10476, ['Brian', 'Vidales', '2128 Copperhead Road', 'Cromwell', 'Connecticut', '6416', 'US', 'Whicessis', '9/19/1977'])
(12063, ['Kristen', 'Pacheco', '57 Patterson Street', 'Houston', 'Texas', '77002', 'US', 'Montwely', '8/13/1984'])
(22041, ['Annette', 'Goodin', '1365 Jefferson Street', 'Portsmouth', 'Virginia', '23707', 'US', 'Ponerver', '9/8/1972'])
(22234, ['George', 'Bacher', '3585 Asylum Avenue', 'Naugatuck', 'Connecticut', '6770', 'US', 'Fortent', '8/29/1966'])
(24975, ['Henry', 'Berkey', '3089 Prospect Street', 'Camden'

(38920, ['Scott', 'Delarosa', '3191 Ruckman Road', 'Oklahoma City', 'Oklahoma', '73008', 'US', 'Shaticut1971', '4/12/1971'])
(752, ['James', 'Lopez', '1538 Farnum Road', 'New York', 'New York', '10011', 'US', 'Thenut', '9/3/1936'])
(6121, ['Ann', 'Wilson', '4490 Fairmont Avenue', 'Warrensburg', 'Missouri', '64093', 'US', 'Takey1978', '9/12/1978'])
(6142, ['Charles', 'Hinton', '3857 Bruce Street', 'Hazelwood', 'Missouri', '63042', 'US', 'Preal1931', '9/23/1931'])
(6172, ['Herman', 'Eddings', '1893 Ruckman Road', 'Stillwater', 'Oklahoma', '74074', 'US', 'Priout', '5/8/1947'])
(6208, ['Tina', 'Mason', '1538 Grove Street', 'New York', 'New York', '10017', 'US', 'Witabir32', '5/15/1932'])
(7427, ['Willie', 'Manson', '291 Haymond Rocks Road', 'Paulina', 'Oregon', '97751', 'US', 'Astion', '6/11/1969'])
(9148, ['Melissa', 'Frink', '2310 Hart Street', 'Hartford', 'Connecticut', '6103', 'US', 'Syrs1990', '10/20/1990'])
(13287, ['Leona', 'Shivers', '2483 Hog Camp Road', 'Palos Park', 'Illinois', 

...

(37522, ['Mary', 'Morrow', '4359 Ventura Drive', 'Santa Cruz', 'California', '95060', 'US', 'Majesigh1955', '8/29/1955'])
(37524, ['Mary', 'Hoover', '788 Ocello Street', 'San Diego', 'California', '92111', 'US', 'Hinging75', '4/28/1975'])
(44537, ['Kim', 'Walker', '3801 May Street', 'Somerset', 'Kentucky', '42501', 'US', 'Hisonecks', '12/30/1974'])
(38566, ['Sylvia', 'Umberger', '4924 Langtown Road', 'Mansfield', 'Ohio', '44902', 'US', 'Thele1946', '3/10/1946'])
(37542, ['James', 'Witt', '4418 Plainfield Avenue', 'Utica', 'New York', '13502', 'US', 'Frocarephey86', '11/4/1986'])
(37546, ['Michelle', 'Miller', '722 Stiles Street', 'Braddock', 'Pennsylvania', '15104', 'US', 'Olly1974', '3/5/1974'])
(37550, ['Andrew', 'Petro', '1681 Caynor Circle', 'Hampton', 'New Jersey', '8827', 'US', 'Thork1968', '3/6/1968'])
(37553, ['Jennifer', 'Lewis', '459 Lochmere Lane', 'Hartford', 'Connecticut', '6103', 'US', 'Houte1946', '5/2/1946'])
(37554, ['Keith', 'Macey', '371 Blue Spruce Lane', 'Hanover',

(40170, ['Doug', 'Walters', '3031 Prudence Street', 'Detroit', 'Michigan', '48219', 'US', 'Plinste', '2/22/1986'])
(40686, ['Sam', 'Thomsen', '3130 Melody Lane', 'Richmond', 'Virginia', '23219', 'US', 'Lizintacer', '12/26/1944'])
(40174, ['Steven', 'Evans', '2622 Courtright Street', 'Carson', 'North Dakota', '58529', 'US', 'Eling1961', '4/13/1961'])
(40175, ['Jessica', 'Noel', '4753 Chandler Hollow Road', 'Pittsburgh', 'Pennsylvania', '15213', 'US', 'Tily1968', '10/7/1968'])
(40176, ['Elena', 'Elledge', '1156 Burning Memory Lane', 'Philadelphia', 'Pennsylvania', '19108', 'US', 'Ortabow', '9/4/1949'])
(40177, ['Kim', 'Mann', '4526 Jones Avenue', 'Winston Salem', 'North Carolina', '27107', 'US', 'Regractools', '8/17/1932'])
(40179, ['Michael', 'Tedesco', '2714 Nelm Street', 'Washington', 'Virginia', '20011', 'US', 'Whemighthis', '2/8/1957'])
(40184, ['Michael', 'Nowell', '260 Tree Top Lane', 'Plymouth Meeting', 'Pennsylvania', '19462', 'US', 'Ounpat', '6/3/1960'])
(40900, ['Steven', 'Kum

(44170, ['Elizabeth', 'Baker', '1432 Pearlman Avenue', 'Concord', 'Massachusetts', '1742', 'US', 'Vellut', '12/9/1942'])
(44171, ['Mark', 'Maples', '3160 Hall Street', 'Las Vegas', 'Nevada', '89101', 'US', 'Fortaithe', '7/14/1993'])
(44172, ['Damon', 'Schmitz', '2710 Green Street', 'Nashville', 'Tennessee', '37209', 'US', 'Theausted', '5/19/1975'])
(44174, ['Elva', 'McAnulty', '3486 Camel Back Road', 'Bartlesville', 'Oklahoma', '74003', 'US', 'Oltous1969', '6/23/1969'])
(44195, ['Douglas', 'Davis', '1522 Commerce Boulevard', 'Omaha', 'Nebraska', '68102', 'US', 'Fecied', '4/3/1941'])
(44231, ['Wilma', 'Tillson', '2546 Hill Haven Drive', 'Waco', 'Texas', '76710', 'US', 'Movell', '11/22/1941'])
(44216, ['Bryan', 'Jones', '3042 Coffman Alley', 'Madisonville', 'Kentucky', '42431', 'US', 'Appis1970', '5/5/1970'])
(44179, ['Miguel', 'Lockwood', '611 Hornor Avenue', 'Claremore', 'Oklahoma', '74017', 'US', 'Shose1935', '3/26/1935'])
(44527, ['Robyn', 'Dutton', '2255 White Avenue', 'Corpus Chris

(47060, ['Ella', 'Medlin', '722 Hoffman Avenue', 'Brooklyn', 'New York', '11206', 'US', 'Wituare', '4/26/1950'])
(47062, ['Dina', 'Champion', '2919 Elmwood Avenue', 'Newark', 'Pennsylvania', '19714', 'US', 'Faut1953', '12/2/1953'])
(47063, ['Leroy', 'Breeden', '304 Don Jackson Lane', 'Honolulu', 'Hawaii', '96826', 'US', 'Forietincee', '12/10/1930'])
(47067, ['Roy', 'Rodriguez', '4248 Woodbridge Lane', 'Southfield', 'Michigan', '48075', 'US', 'Lonat1962', '9/23/1962'])
(47069, ['Virginia', 'Glaze', '4060 Lowndes Hill Park Road', 'Bakersfield', 'California', '93301', 'US', 'Fordoon', '7/26/1960'])
(47070, ['Barbara', 'Price', '281 Chandler Hollow Road', 'Bridgeville', 'Pennsylvania', '15017', 'US', 'Beffele', '1/23/1993'])
(47072, ['Sally', 'Humphrey', '3216 Dola Mine Road', 'Morrisville', 'North Carolina', '27560', 'US', 'Exclick', '7/29/1933'])
(47073, ['Randall', 'Slavin', '1878 Maloy Court', 'Milford', 'Kansas', '66514', 'US', 'Aday1932', '8/8/1932'])
(47075, ['Gloria', 'Young', '473

(49741, ['Reta', 'Torres', '789 American Drive', 'Blackwood', 'New Jersey', '8012', 'US', 'Agne1956', '10/2/1956'])
(49756, ['Olga', 'Mercer', '3476 Tator Patch Road', 'Chicago', 'Illinois', '60654', 'US', 'Bableand', '7/18/1946'])
(49772, ['James', 'Heald', '4249 Maple Court', 'Laddonia', 'Missouri', '63352', 'US', 'Threpar', '12/13/1930'])
(49773, ['Donald', 'Daniels', '1882 Berkshire Circle', 'Knoxville', 'Tennessee', '37917', 'US', 'Welle1987', '2/10/1987'])
(49777, ['Nicole', 'Jenkins', '768 Ripple Street', 'Saginaw', 'Michigan', '48607', 'US', 'Hundrace', '7/16/1932'])
(49781, ['Joseph', 'Cohen', '3181 Park Boulevard', 'Des Moines', 'Iowa', '50309', 'US', 'Arday1942', '11/11/1942'])
(49793, ['James', 'Coleman', '2201 Payne Street', 'Houston', 'Texas', '77063', 'US', 'Plentanne', '12/17/1930'])
(49795, ['Curtis', 'Smith', '754 Hedge Street', 'Red Bank', 'New Jersey', '7701', 'US', 'Lumn1984', '7/18/1984'])
(49803, ['Edward', 'Ulm', '2042 Half and Half Drive', 'Selma', 'California'

In [10]:
result = list()

for x in top_ten_mutual_friends_rdd:
    friend_count = x[0]
    friend1 = int(x[1].split(', ')[0])
    friend2 = int(x[1].split(', ')[1])
    
    friend1_data = friends_details_rdd.lookup(friend1)[0]
    friend2_data = friends_details_rdd.lookup(friend2)[0]
    
    line = str(friend_count) +\
            '\t' + friend1_data[0] + '\t' + friend1_data[1] +\
            '\t' + friend1_data[2] + '\t' + friend2_data[0] +\
            '\t' + friend2_data[1] + '\t' + friend2_data[2]
    
    #print(line)
    result.append(line)
    
sc.parallelize(result).saveAsTextFile('spark_rdd_version/top_ten_mutual_friends.txt')